In [3]:
import keras 
import pandas as pd
import matplotlib.pyplot as plt 
import keras 
from keras.preprocessing.image import ImageDataGenerator
from keras.preprocessing import image 
import os
import numpy as np
import math
import dlib
import cv2
import easydict
import csv
import pandas as pd
from sklearn.model_selection import train_test_split
from keras.models import Sequential
from keras.layers import Convolution2D, MaxPooling2D, ZeroPadding2D
from keras.layers import Activation, Dropout, Flatten, Dense
from keras.regularizers import l2
from keras import layers
from keras.utils import to_categorical

Using TensorFlow backend.


In [4]:
from sklearn.preprocessing import LabelEncoder,OneHotEncoder 

In [5]:
args={"shape_predictor":"shape_predictor_68_face_landmarks.dat"}

In [6]:
detector=dlib.get_frontal_face_detector()
predictor=dlib.shape_predictor(args["shape_predictor"])

In [7]:
def rect_to_bb(rect):
    x=rect.left()
    y=rect.top()
    w=rect.right()-x
    h=rect.bottom()-y
    return (x,y,w,h)

In [8]:
def shape_to_np(shape,dtype='int'):
    coords=np.zeros((68,2),dtype=dtype)
    for i in range(0,68):
        coords[i]=(shape.part(i).x,shape.part(i).y)
    return coords

In [9]:
def preprocess_dis(dis_array):
    x=dis_array-np.mean(dis_array)
    if np.std(dis_array)!=0:
        x/=np.std(dis_array)
    return x

In [10]:
def convert_points_to_distance(points):

    mid_x=(points[14,0]+points[18,0])/2
    mid_y=(points[14,1]+points[18,1])/2
    mid_point=np.array([mid_x,mid_y])
    points=(points-mid_point)**2
    distances_array=np.sqrt((points[:,0]+points[:,1]))
    
    return preprocess_dis(distances_array)
    

In [11]:
def face_landmarks(image):
    #all_images=[]
    #for image in images:
    gray=cv2.cvtColor(image,cv2.COLOR_BGR2GRAY)
    rects=detector(gray,1)
    shape=np.zeros((20,2))
    for rect in rects:
        shape=predictor(gray,rect)
        shape=shape_to_np(shape)
        shape=shape[48:68]
    #all_images.append(shape)

    return shape   

In [12]:
def empty_distance(number):
    shape=np.zeros((20,number))
    return shape

In [13]:
lip_data = []

In [14]:
labels=[]
datagen=ImageDataGenerator()
train_dir="C:\\Users\\this pc\\Desktop\\Minor\\Data"
for label in os.listdir(train_dir):
    labels_dir=os.path.join(train_dir,label)
    for repeat in os.listdir(labels_dir):       
        word_dir=os.path.join(labels_dir,repeat)
        for sub in os.listdir(word_dir):
            first_dir = os.path.join(word_dir, sub)
            print(repeat)
            if(repeat == "phrases"):
                val = "P"
            else:
                val = "W"
            for sec_sub in os.listdir(first_dir):
                sec_dir = os.path.join(first_dir, sec_sub)
                print("currently in %", sec_dir)
                images_array=[]
                num_images=0
                for image_dir in os.listdir(sec_dir):
                    if num_images==10:
                        break
                    image=cv2.imread(os.path.join(sec_dir,image_dir))
                    points=face_landmarks(image)
                    points=convert_points_to_distance(points)
                    #if points is not None:
                    images_array.append(points)
                    print(points)
                    num_images=num_images+1
                if num_images<10:
                    np.append(images_array,empty_distance(10-num_images))
                lip_data=np.append(lip_data,np.array(images_array))
                label1 = str(val) + str(int(sub)-1)
                labels.append(label1)

words
currently in % C:\Users\this pc\Desktop\Minor\Data\F01\words\01\01
[ 1.63863431  0.41678409 -0.355377   -0.85098294 -0.19631413  0.66590639
  1.89675078  0.62383619  0.00624126 -0.33156885  0.00624126  0.62383619
  1.1232585  -0.97008945 -1.63010407 -0.71304503  1.35923104 -0.71304503
 -1.63010407 -0.97008945]
[ 1.52286208  0.38968793  0.02198601 -0.42522769  0.14556404  0.64005922
  1.78901241  0.76371688  0.14556404  0.12833234  0.14556404  0.52522965
  0.68189236 -1.08796323 -1.80912775 -0.84810992  1.23545239 -0.94471454
 -1.80912775 -1.21065251]
[ 1.42136591  0.43475147  0.07483343 -0.44300005  0.07483343  0.67038329
  1.68770391  0.79864205  0.31575902  0.08967594  0.43475147  0.94370353
  0.62235193 -1.1162663  -1.77469003 -1.1162663   0.88868992 -1.1162663
 -1.77469003 -1.1162663 ]
[ 1.78070915  0.54669377 -0.24966854 -0.69908247 -0.24966854  0.54669377
  2.004883    0.43844209 -0.56301088 -0.92378943 -0.56301088  0.43844209
  1.33262678 -0.66261755 -1.37320335 -0.6626175

[ 1.57590991  0.69695684 -0.279819   -0.63153372 -0.279819    0.69695684
  1.82798927  0.69695684 -0.06848104 -0.14099069  0.05931123  0.81371494
  1.09353353 -1.02320186 -1.61261978 -0.85937433  1.09353353 -1.02320186
 -1.61261978 -1.02320186]
[ 1.5809883   0.61391928 -0.01087381 -0.61636264 -0.01087381  0.61391928
  1.82128037  0.73661957 -0.01087381 -0.10357145 -0.01087381  0.73661957
  1.05249724 -0.97447606 -1.64194503 -0.97447606  1.05249724 -1.10603466
 -1.64194503 -1.10603466]
[ 1.62254821  0.44611112 -0.04345015 -0.6085467  -0.04345015  0.69861135
  1.86674264  0.71130503  0.19823795 -0.06050992  0.19823795  0.71130503
  0.77397501 -1.02720955 -1.70462026 -1.02720955  1.04696133 -1.02720955
 -1.70462026 -1.02720955]
[ 1.65717574  0.49489612 -0.12802206 -0.69225424 -0.12802206  0.57235101
  1.88480823  0.57235101 -0.319294   -0.4470143  -0.12802206  0.67184533
  1.16994745 -0.80724016 -1.673214   -0.80724016  1.39464246 -0.80724016
 -1.673214   -0.80724016]
[0. 0. 0. 0. 0. 0. 0

[ 1.33951679  0.37237554 -0.18890606 -0.67694312 -0.06598279  0.59896629
  1.84056085  0.83877355  0.1503021   0.07609517  0.1503021   0.83877355
  0.83877355 -1.17896864 -1.68099416 -0.97038911  1.33951679 -0.97038911
 -1.68099416 -0.97038911]
[ 1.71082485  0.63048513 -0.30251176 -0.63846268 -0.30251176  0.74201015
  1.73027322  0.63048513 -0.10064594 -0.4041842   0.0214187   0.63048513
  1.24307923 -1.0125763  -1.5755766  -0.8560915   1.26493647 -1.0125763
 -1.5755766  -0.82328437]
[ 1.51984616  0.43874935 -0.30602842 -0.64930877 -0.30602842  0.64328401
  1.97178602  0.85081423  0.0092634  -0.42255318 -0.11381603  0.43874935
  1.06832255 -0.98472626 -1.55633115 -0.82463347  1.51984616 -0.77488103
 -1.55633115 -0.96602334]
[ 1.57423036  0.65609331 -0.15686494 -0.77908466 -0.28405692  0.65609331
  1.83615883  0.65609331  0.05294348 -0.28405692  0.05294348  0.65609331
  1.07947862 -0.87727891 -1.52162628 -0.89769398  1.3268453  -1.22040423
 -1.52162628 -1.00428022]
[ 1.4833597   0.53289

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
currently in % C:\Users\this pc\Desktop\Minor\Data\F01\words\02\02
[ 1.74263999  0.55112848  0.11188669 -0.39389833  0.11188669  0.55112848
  1.71172384  0.68206663  0.11188669 -0.11458345  0.25067624  0.68206663
  0.87423766 -1.0608512  -1.76738255 -0.95129383  0.87423766 -1.10008688
 -1.76738255 -1.10008688]
[ 0.96767419  0.3777144   0.06865298 -0.09352148  0.33142627  0.3777144
  1.24195778  0.87934922  0.86652362  0.74858276  0.95520778  1.07773815
  0.4231855  -1.25728091 -1.77772995 -1.25728091  0.36237798 -1.25728091
 -1.77772995 -1.25728091]
[ 1.24865173  0.23017567  0.311764    0.12434576  0.61544009  0.39088757
  1.12828629  0.7901619   0.61544009  0.46775712  0.73879738  1.01939738
  0.52404067 -1.22056233 -1.82202351 -1.22056233  0.52404067 -1.32200732
 -1.82202351 -1.32200732]
[ 1.29886003  0.26005044  0.34326765  0.15210767  0.34326765  0.26005044
  

[ 1.81372867  0.58138897 -0.27977352 -0.68026322 -0.23769117  0.41809935
  1.74552771  0.51485094 -0.23769117 -0.4385463  -0.09938744  0.84149709
  1.29348232 -0.68026322 -1.64713088 -0.92198013  1.26352622 -0.92198013
 -1.64713088 -0.68026322]
[ 1.52525836  0.27160808 -0.22773658 -0.4203708   0.1405713   0.62653344
  1.75566021  0.62653344  0.1405713  -0.14836692  0.1405713   0.88977771
  0.95198696 -1.19224228 -1.78039018 -0.83595574  1.21165246 -0.96437855
 -1.78039018 -0.93089335]
[ 1.34441931  0.33583448  0.01013263 -0.55307114 -0.10877456  0.45008091
  1.30162991  0.91558814  0.78062425  0.57333639  0.78062425  1.10258415
  0.79313065 -1.18047961 -1.67947867 -1.28379287  0.43605328 -1.28379287
 -1.67947867 -1.05516995]
[ 1.37579412  0.40943053  0.20885372 -0.27475026  0.20885372  0.28361631
  0.98037249  0.87748511  0.49579237  0.6608842   0.89238845  1.31073719
  0.5463373  -1.23901677 -1.80732776 -1.23901677  0.40943053 -1.33487051
 -1.80732776 -0.95766622]
[ 1.4191938   0.3899

...

[ 1.96718452  0.60574643 -0.11270466 -0.84988375 -0.2949575   0.43082309
  1.65882535  0.43082309 -0.2949575  -0.57242063 -0.11270466  0.79943252
  1.38240727 -0.53826335 -1.68227314 -0.80485769  1.09235814 -0.84988375
 -1.68227314 -0.57242063]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
currently in % C:\Users\this pc\Desktop\Minor\Data\M08\words\09\07
[ 2.00868323  0.56788041 -0.04918065 -0.78338073 -0.22756699  0.36214342
  1.69533715  0.47666674 -0.22756699 -0.49212364 -0.04918065  0.87060417
  1.4306979  -0.62868568 -1.65715201 -0.91695669  0.82257539 -0.91695669
 -1.65715201 -0.62868568]
[ 1.80752881  0.71291254 -0.26618192 -1.10527357 -0.28538907  0.56127755
  1.80752881  0.48772981 -0.28538907 -0.6395356  -0.12098013  0.77975665
  1.34208909 -0.51729386 -1.57101154 -0.74872114  1.10940648 -0.74872114
 -1.57101154 -0.74872114]
[ 1.79194659  0.71931142 -0.19681853 -0.80883181 -0.32192414  0.71931142
  1.55124244  0.50213405  0.00954834 -0.32192414  0.14169133  0

[ 1.79706791  0.86869734 -0.12540008 -0.74550697 -0.12540008  0.78104176
  1.53744802  0.51447714 -0.12540008 -0.22033568  0.01712735  0.75133068
  1.24353031 -0.94853504 -1.53326392 -0.94853504  1.01945265 -1.11226618
 -1.53326392 -1.11226618]
[ 1.6497526   0.79773287 -0.15257646 -0.7591018  -0.15257646  0.79773287
  1.6497526   0.67196001 -0.0149175  -0.2306845   0.08117151  0.67196001
  1.12543138 -1.00453372 -1.55172776 -1.00453372  1.12543138 -0.96753533
 -1.55172776 -1.18101019]
[ 1.50351746  0.6627655   0.26891744 -0.37789127  0.26891744  0.6627655
  1.50351746  0.6627655   0.26891744 -0.03641372  0.26891744  0.85204312
  0.82115857 -1.12399481 -1.74380145 -0.88300578  0.82115857 -1.3282265
 -1.74380145 -1.3282265 ]
[ 1.48073846  0.64450372  0.25225248 -0.24527429  0.38925329  0.83400038
  1.48073846  0.83400038  0.04732871  0.13722228  0.04732871  0.83400038
  0.7169378  -1.39276397 -1.77526053 -0.85530855  0.7169378  -1.1856875
 -1.77526053 -1.1856875 ]
[ 1.58780921  0.645381 

[ 1.38268813  0.44710275  0.2228305  -0.43797944  0.2228305   0.8993385
  1.71282867  0.73902414  0.39261841  0.2421993   0.2228305   0.6220403
  0.72256545 -1.29533909 -1.75959932 -0.82948524  0.72256545 -1.1741211
 -1.75959932 -1.29533909]
[ 1.79423897  0.55192352 -0.28961561 -0.80809027 -0.28961561  0.62912245
  1.78428301  0.62912245 -0.11933447 -0.54885294 -0.28961561  0.7328869
  1.27756762 -0.80809027 -1.58580225 -0.76602184  1.26580835 -0.76602184
 -1.58580225 -0.80809027]
[ 1.78812815  0.51076909 -0.09769281 -0.7806876  -0.26031059  0.62452978
  1.78812815  0.51076909 -0.09769281 -0.21226523 -0.01098575  0.62452978
  1.22168281 -0.74569961 -1.63332116 -1.01877766  1.22168281 -0.7806876
 -1.63332116 -1.01877766]
[ 1.85188978  0.55428561 -0.1865652  -0.92498586 -0.37157235  0.61779523
  1.83178624  0.55428561 -0.1865652  -0.66267626 -0.37157235  0.70976027
  1.30762501 -0.78297636 -1.44960506 -0.78297636  1.30762501 -0.78297636
 -1.44960506 -0.78297636]
[0. 0. 0. 0. 0. 0. 0. 0. 

[ 1.86113139  0.45456623 -0.20306643 -0.67353371 -0.06025798  0.45456623
  1.88011077  0.61680479 -0.26815544 -0.4069773  -0.26815544  0.45456623
  1.32841479 -0.97898017 -1.47320293 -0.73430807  1.35053216 -0.79851431
 -1.47320293 -1.06233788]
[ 1.96324429  0.48196922 -0.2774036  -1.02133787 -0.46521212  0.52758566
  1.70642111  0.60143168 -0.2774036  -0.52538169 -0.11451814  0.60143168
  1.46875757 -0.77335978 -1.51729405 -0.77335978  1.21046493 -0.77335978
 -1.51729405 -0.52538169]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
currently in % C:\Users\this pc\Desktop\Minor\Data\M08\words\10\09
[ 1.75885751  0.47942375 -0.31188319 -0.96680153 -0.31188319  0.47942375
  2.01119047  0.68657642 -0.06399477 -0.34595884 -0.06399477  0.84036554
  1.08947411 -0.79874523 -1.58764423 -0.79874523 

ValueError: cannot reshape array of size 299960 into shape (1500,10,20)

In [41]:
lip_data.reshape((1500,10,20))

ValueError: cannot reshape array of size 299960 into shape (1500,10,20)

In [18]:
len(labels), lip_data.shape

(1500, (299960,))

In [21]:
labelencoder=LabelEncoder()

In [23]:
labels_enc = labelencoder.fit_transform(labels) 

In [26]:
import h5py

In [28]:
with h5py.File('C:\\Users\\this pc\\Desktop\\Minor\\hdf5_data.h5', 'w') as hdf:
    hdf.create_dataset('lipdata', data = lip_data)
    hdf.create_dataset('labels', data = labels_enc)

In [ ]:
f=open("dataset.txt",'w')
f.write(str(lip_data))
f.close()

In [ ]:
f=open("dataset.txt")
d=f.read()
f.close()